# Creating dense point density and confidence binning

In [ ]:
import pdal
pdal.__version__
import json
import pandas as pd
import numpy as np
from pathlib import Path # KW_dense_cloud-22-58.las
import geopandas as gpd
from shapely.geometry import Point
from shapely import wkt
from osgeo import gdal
import rasterio
import rioxarray as rxr
from rasterio.features import shapes

In [ ]:
def get_bin_statistics(array, length=1):
    df = pd.DataFrame(array)
    metadata = {
        "bin_x": np.floor(df.loc[:,"X"].min())+length/2,
        "bin_y": np.floor(df.loc[:,"Y"].min())+length/2,
        "bin_count": len(array),
        "bin_conf_sum": df.loc[:,"confidence"].sum()
    }
    
    return metadata

def get_bin_statistics_without_conf(array, length=1):
    df = pd.DataFrame(array)
    metadata = {
        "bin_x": np.floor(df.loc[:,"X"].min())+length/2,
        "bin_y": np.floor(df.loc[:,"Y"].min())+length/2,
        "bin_count": len(array),
        #"bin_conf_sum": df.loc[:,"Confidence"].sum()
    }
    
    return metadata

In [ ]:
!pdal info ..\export\points\take2\KW_sparse_cloud-processed.las --stats

# Dense Cloud - filtered


In [ ]:
# Dense cloud folder path
dc_data = Path(r"..\export\points\dense_cloud")

In [ ]:
data = dc_data
for file_name in ["KW_dense_cloud_10-255.las"]:
    output = pd.DataFrame()
    for path in [i for i in data.glob(file_name)]:
        args = [
                {
                    "type" : "readers.las",
                    "filename" : f"{str(Path(data,path.name))}",
    #                "in_srs" : "EPSG:32633",
                    "extra_dims" : ["confidence=uint8", "normal=uint8"] # for dense cloud
                },
                {
                    "type":"filters.splitter",
                    "length":"1",
                    "origin_x":"500000.0",
                    "origin_y":"8680000.0"
                }
            ]

        pipeline = pdal.Pipeline(json.dumps(args))
        count = pipeline.execute()
        arrays = pipeline.arrays
        metadata = pipeline.metadata
        log = pipeline.log
        for array in arrays:
            output = output.append(get_bin_statistics(array), ignore_index=True)
            
    compiled_output = output.groupby(["bin_x","bin_y"]).sum().reset_index()
    compiled_output
    compiled_output["bin_conf_mean"] = compiled_output.bin_conf_sum/compiled_output.bin_count
    gdf = gpd.GeoDataFrame(compiled_output, geometry=[Point(xy) for xy in zip(compiled_output.bin_x,compiled_output.bin_y)])
    gdf.crs = "epsg:32633"
    gdf.to_file(Path(data,path.name).with_suffix(".gpkg"), driver="GPKG")

# Dense Cloud - raw

In [ ]:
data = dc_data
data_name = "KW_dense_cloud"
file_name = f"{data_name}-*-*.las"
output = pd.DataFrame()
for path in [i for i in data.glob(file_name)]:
    prasint(path.name)
    args = [
            {
                "type" : "readers.las",
                "filename" : f"{str(Path(data,path.name))}",
#                "in_srs" : "EPSG:32633",
                "extra_dims" : "Confidence=uint8"
            },
            {
                "type":"filters.splitter",
                "length":"1",
                "origin_x":"500000.0",
                "origin_y":"8680000.0"
            }
        ]



    pipeline = pdal.Pipeline(json.dumps(args))
    count = pipeline.execute()
    arrays = pipeline.arrays
    metadata = pipeline.metadata
    log = pipeline.log
    for array in arrays:
        output = output.append(get_bin_statistics(array), ignore_index=True)

In [ ]:
compiled_output = output.groupby(["bin_x","bin_y"]).sum().reset_index()
compiled_output
compiled_output["bin_conf_mean"] = compiled_output.bin_conf_sum/compiled_output.bin_count

In [ ]:
gdf = gpd.GeoDataFrame(compiled_output, geometry=[Point(xy) for xy in zip(compiled_output.bin_x,compiled_output.bin_y)])
gdf.crs = "epsg:32633"
gdf.to_file(Path(data,data_name).with_suffix(".gpkg"), driver="GPKG")

## Sparse Cloud

In [ ]:
sc_data = Path(r"..\export\points\sparse_cloud")

In [ ]:
data = sc_data
for file_name in ["KW_sparse_cloud-raw.las", "KW_sparse_cloud-processed.las"]:
    output = pd.DataFrame()
    for path in [i for i in data.glob(file_name)]:
        args = [
                {
                    "type" : "readers.las",
                    "filename" : f"{str(Path(data,path.name))}",
    #                "in_srs" : "EPSG:32633",
                    "extra_dims" : "normal=uint8"
                },
                {
                    "type":"filters.splitter",
                    "length":"1",
                    "origin_x":"500000.0",
                    "origin_y":"8680000.0"
                }
            ]

        pipeline = pdal.Pipeline(json.dumps(args))
        count = pipeline.execute()
        arrays = pipeline.arrays
        metadata = pipeline.metadata
        log = pipeline.log
        for array in arrays:
            output = output.append(get_bin_statistics_without_conf(array), ignore_index=True)
            
    compiled_output = output.groupby(["bin_x","bin_y"]).sum().reset_index()
    compiled_output
    gdf = gpd.GeoDataFrame(compiled_output, geometry=[Point(xy) for xy in zip(compiled_output.bin_x,compiled_output.bin_y)])
    gdf.crs = "epsg:32633"
    gdf.to_file(Path(data,path.name).with_suffix(".gpkg"), driver="GPKG")

## Creating extent of the point clouds
make sure to change the filename and data directory below first

In [ ]:
data = sc_data # or dc_data
filenames =  ["KW_dense_cloud-*-*.las"] #["KW_dense_cloud_10-255.las","KW_dense_cloud-*-*.las","KW_sparse_cloud-processed.las","KW_sparse_cloud-raw.las"]

In [ ]:
for file_name in filenames: 
    file_path = Path(data,file_name)
    if len([i for i in data.glob(file_name)]) > 1:
        args = [
            f"{str(file_path)}",
            {
                "type":"filters.merge",
                "tag":"merged"
            },
            {
                "type": "filters.hexbin",
                "inputs": ["merged"],
                "edge_length": 0.6204
            }
            ]
    elif len([i for i in data.glob(file_name)]) == 1:
        args = [
            f"{str(file_path)}",
            {
                "type": "filters.hexbin",
                "edge_length": 0.6204
            }
            ]

    pipeline = pdal.Pipeline(json.dumps(args))
    count = pipeline.execute()
    arrays = pipeline.arrays
    metadata = pipeline.metadata
    log = pipeline.log

    geom = json.loads(metadata)["metadata"]['filters.hexbin']["boundary"]
    geometry=wkt.loads(geom)
    boundary = gpd.GeoDataFrame(geometry=[geometry], crs="epsg:32633")
    boundary.to_file(Path(file_path.parent,"KW_dense_cloud_raw_boundary").with_suffix(".gpkg"), driver="GPKG")
    with open(Path(file_path.parent,"KW_dense_cloud_raw_boundary_metadata").with_suffix(".json"), 'w', encoding='utf-8') as f:
        json.dump(json.loads(metadata), f, ensure_ascii=False, indent=4)

# Import mesh and export vertices as LAS points

## Create Point cloud frm mesh

In [ ]:
mesh_data = Path(r"..\export\model")

In [ ]:
data = mesh_data
data_name = Path("KW_mesh_10-255.obj")

args = [
    {
        "type": "readers.obj",
        "filename": str(Path(data,data_name))
    },
    {
        "type" : "writers.las",
        "filename": str(Path(data,file_name.stem+"_model").with_suffix(".las")),
        "a_srs": "EPSG:32633",
        "scale_x": "auto",
        "scale_y": "auto",
        "scale_z": "auto",
        "offset_x": "auto",
        "offset_y": "auto",
        "offset_z": "auto"
    }
]


pipeline = pdal.Pipeline(json.dumps(args))
count = pipeline.execute()
arrays = pipeline.arrays
metadata = pipeline.metadata
log = pipeline.log


## Calculate point density for mesh

In [ ]:
data = mesh_data
data_name = Path("KW_mesh_10-255.obj")

output = pd.DataFrame()

args = [
        {
            "type" : "readers.obj",
            "filename" : f"{str(Path(data,data_name))}",
        },
        {
            "type":"filters.splitter",
            "length":"1",
            "origin_x":"500000.0",
            "origin_y":"8680000.0"
        }
    ]



pipeline = pdal.Pipeline(json.dumps(args))
count = pipeline.execute()
arrays = pipeline.arrays
metadata = pipeline.metadata
log = pipeline.log
for array in arrays:
    output = output.append(get_bin_statistics_without_conf(array), ignore_index=True)
    
compiled_output = output.groupby(["bin_x","bin_y"]).sum().reset_index()

gdf = gpd.GeoDataFrame(compiled_output, geometry=[Point(xy) for xy in zip(compiled_output.bin_x,compiled_output.bin_y)])
gdf.crs = "epsg:32633"
gdf.to_file(Path(data,data_name).with_suffix(".gpkg"), driver="GPKG")

with open(Path("data","boundaries",data_name.stem+"_model_metadata").with_suffix(".json"), 'w', encoding='utf-8') as f:
    json.dump(json.loads(metadata), f, ensure_ascii=False, indent=4)

## Calculate boundary from obj
(Could probably all be chained together in a more advanced chain...)

In [ ]:
data = mesh_data
data_name = Path("KW_mesh_10-255.obj")

args = [
        {
            "type": "readers.obj",
            "filename": str(Path(data,data_name))
        },
        {
            "type": "filters.hexbin",
            "edge_length": 0.6204
        }
        ]

pipeline = pdal.Pipeline(json.dumps(args))
%time count = pipeline.execute()
arrays = pipeline.arrays
metadata = pipeline.metadata
log = pipeline.log

geom = json.loads(metadata)["metadata"]['filters.hexbin']["boundary"]
geometry=wkt.loads(geom)
boundary = gpd.GeoDataFrame(geometry=[geometry], crs="epsg:32633")
boundary.to_file(Path("data","boundaries",data_name.stem+"_model_boundary").with_suffix(".gpkg"), driver="GPKG")
with open(Path("data","boundaries",data_name.stem+"_model_boundary_metadata").with_suffix(".json"), 'w', encoding='utf-8') as f:
    json.dump(json.loads(metadata), f, ensure_ascii=False, indent=4)

# Boundary for DEM

In [ ]:
dem_data = Path(r"..\export\dem")

In [ ]:
data = dem_data
data_name = Path("KW_dem_10-255.tif")
      
#!pdal translate -i "//svalbox/metashape-processing$/Konusdalen-West/export/dem/KW_dem_10-255.tif" -o "./data/KW_dem_10-255_filtered.las" -f range --filters.range.limits="band_1[0:400]"    

args = [
        {
            "type": "readers.las",
            "filename": "./data/KW_dem_10-255_filtered.las"
        },
        {
            "type": "filters.hexbin",
            "edge_length": 0.6204
        }
        ]

pipeline = pdal.Pipeline(json.dumps(args))
pipeline.execute()
arrays = pipeline.arrays
metadata = pipeline.metadata
log = pipeline.log



geom = json.loads(metadata)["metadata"]['filters.hexbin']["boundary"]
geometry=wkt.loads(geom)
boundary = gpd.GeoDataFrame(geometry=[geometry], crs="epsg:32633")
boundary.to_file(Path("data","boundaries",data_name.stem+"_model_boundary").with_suffix(".gpkg"), driver="GPKG")
with open(Path("data","boundaries",data_name.stem+"_model_boundary_metadata").with_suffix(".json"), 'w', encoding='utf-8') as f:
    json.dump(json.loads(metadata), f, ensure_ascii=False, indent=4)